(reservoir)=
# reservoir
A reservoir that is part of a regulated hydropower watercourse

|   |   |
|---|---|
|Input connections|{ref}`plant`, {ref}`gate`, {ref}`junction`, {ref}`volume_constraint`, {ref}`cut_group`, {ref}`inflow_series`, {ref}`tunnel`, {ref}`river`|
|Output connections|{ref}`plant`, {ref}`river`, {ref}`gate`, {ref}`tunnel`, {ref}`cut_group`, {ref}`inflow_series`, {ref}`junction_gate`, {ref}`junction`, {ref}`creek_intake`, {ref}`volume_constraint`|
|License|SHOP_OPEN|
|Release version|13.0.0.a|

```{contents}
:local:
:depth: 1
```

## Introduction
The reservoir is the storage element in hydro system modelling where the following attributes are mandatory:
- [max_vol](reservoir:max_vol): Maximum volum of the reservoir at the point of forced overflow.
- [lrl](reservoir:lrl): Lower regulated level.
- [hrl](reservoir:hrl): Higher regulated level.
- [vol_head](reservoir:vol_head): The relation between reservoir volume and head.
- [start_head](reservoir:start_head) / [start_vol](reservoir:start_vol): The reservoir level at the beginning of the optimisation, either given in meter or Mm3.

## Volume and head
The releation between volume and head is required and given by the [vol_head](reservoir:vol_head) attribute, which is a piecewise linear [XY-curve](datatype:xy). The total reservoir volume before forced overflow is given by [max_vol](reservoir:max_vol). The [max_vol](reservoir:max_vol) can either represent only the active volume or the full volume of the reservoir. If only the active volume is considered, [lrl](reservoir:lrl) will coincide with zero volume.

## Overflow
In reservoirs where overflow may occur, it is recommended to also define the [vol_head](reservoir:vol_head) curve for levels above [hrl](reservoir:hrl). Overflow is described with the [flow_descr](reservoir:flow_descr) [XY-curve](datatype:xy), where the x-values represents reservoir levels and the y-values overflow rates in $m^3/s$. The first xy pair must be [hrl](reservoir:hrl) and zero, meaning that there is no overflow at [hrl](reservoir:hrl). The following pair must have increasing x and y values.

To ensure the spilled water is directed to the right reservoir and assigned a reasonable penalty cost, the {ref}`reservoir` should be connected to a {ref}`river` where the river [](river:upstream_elevation) equals the [hrl](reservoir:hrl). Overflow penalty can be given by setting the [flow_cost](river:flow_cost). If the water is spilled to a different reservoir and not the ocean, the river should be connected to this reservoir.

Previously, {ref}`gate` has been used for overflow modelling but river is the recommended way for future compatibility. To model overflow using {ref}`gate`, the upstream reservoir has to been connected to the gate using connection type **SPILL**.

### Physical overflow description
The overflow description is a linear relaxation, hence overflow may occur in siutations where it is not physically possible in special situation. SHOP includes a MIP formulation to prevent this that can be activated using the {ref}`river` [mip_flag](river:mip_flag), {ref}`reservoir` [overflow_mip_flag](reservoir:overflow_mip_flag) or [universal_overflow_mip](global_settings:universal_overflow_mip).

See the [overflow modelling example](reservoir-overflow) for further details.

## Constraints
The user can specify different types of reservoir limits to enforce correct physical behaviour and to enforce different physical and environmental restrictions. Figure 1 illustrates the available reservoir limits and Table 1 gives an overview of which inputs and outputs that relates to the different limits.

|![](./img/reservoir_limits.png)|
|---|
|<b>Figure 1: Overview of reservoir limit types.</b>|

|Attribute|Constraint type|Penalty input|Penalty output|Objective|
|---|---|---|---|---|
|[flow_descr](reservoir:flow_descr) \[meter\]||[overflow_cost](reservoir:overflow_cost)||[nonphysical_spill_cost](objective:nonphysical_spill_cost), [physical_spill_cost](objective:physical_spill_cost)|
|[max_vol](reservoir:max_vol),[hrl](reservoir:hrl)|soft|[penalty_cost](penalty_cost)|[penalty](reservoir:penalty), [endpoint_penalty](reservoir:endpoint_penalty)|[rsv_penalty](objective:rsv_penalty), [rsv_end_penalty](objective:rsv_end_penalty)|
|[max_vol_constr](reservoir:max_vol_constr)|hard|||||
|[tactical_limit_max](reservoir:tactical_limit_max)|soft|[tactical_cost_max](reservoir:tactical_cost_max)|[tactical_penalty_up](reservoir:tactical_penalty_up), [tactical_penalty](reservoir:tactical_penalty)|[rsv_tactical_penalty](objective:rsv_tactical_penalty)|
|[tactical_limit_min](reservoir:tactical_limit_min)|soft|[tactical_cost_min](reservoir:tactical_cost_min)|[tactical_penalty_down](reservoir:tactical_penalty_down), [tactical_penalty](reservoir:tactical_penalty)|[rsv_tactical_penalty](objective:rsv_tactical_penalty)|
|[min_vol_constr](reservoir:min_vol_constr)|hard|||||
|[lrl](reservoir:lrl)|soft|[penalty_cost](penalty_cost)|[penalty](reservoir:penalty), [endpoint_penalty](reservoir:endpoint_penalty), [end_penalty](reservoir:end_penalty)|[rsv_penalty](objective:rsv_penalty), [rsv_end_penalty](objective:rsv_end_penalty)|

The outer limits are typically [max_vol](reservoir:max_vol), [hrl](reservoir:hrl) and [lrl](reservoir:lrl) that represents the physical limts the system is designed and regulated to operate within. These are soft constraints such that SHOP also can provide a solution in situations where the input is overspecified such that no physical solution exist. A penalty will apply in these situations.

The [min_vol_constr](reservoir:min_vol_constr) and [max_vol_constr](reservoir:max_vol_constr) are time dependent operation constraints. These can, for example, be used if the system must be operated within given limits due to maintenance. However, hard constraints should be used carefully since they may cause infeasibility or non-physical behaviour in other parts of the system to fulfill the hard constraints.

Tactical limits, [tactical_limit_min](reservoir:tactical_limit_min) and [tactical_limit_max](reservoir:tactical_limit_max) lets the user specify time dependent soft constraints at a time dependent self defined cost.

## Water value
The value of stored water beyond the optimization horizon will typically come from a seasonal- or long-term model. Details on how to set the water values are described in [tutorial](water-value-descriptions) and [example](individual-water-values).

## Schedule
[Schedule](reservoir:schedule) imposes a specific strategy on a {ref}`reservoir` and limits the way the system can be operated, hence it should be used very carefully. A schedule can be set either for end value or for specific moments through the optimization period.

Further details on the use of reservoir schedule is illustrated in this [example](reservoir-schedule).

### Slack
{ref}`Reservoir <reservoir>` [upper_slack](reservoir:upper_slack) and [lower_slack](reservoir:lower_slack) are limits to apply at the end of the optimization period to validate the water values. Slack should be used in combination with [schedule](reservoir:schedule). The [upper_slack](reservoir:upper_slack) adds a band on top of the schedule, while the [lower_slack](reservoir:lower_slack) adds a band below the schedule value. This functionality is intended to be used in combination with cuts, where the slack values define the area in which the cuts are valid.

## Ramping
Ramping limits how rapid the volume or head in a reservoir can change over time, for example, to avoid excessive wear of the shores of a reservoir. The ramping constraint can be set individually for both up and down direction. It can be set in terms of volume with [volume_ramping_up](reservoir:volume_ramping_up) and [volume_ramping_down](reservoir:volume_ramping_down), or level with [level_ramping_up](reservoir:level_ramping_up) and [level_ramping_down](reservoir:level_ramping_down).


## Examples
  - [](cut-description)
  - [](water-value-descriptions)
  - [](individual-water-values)
  - [](ramping)
  - [](reservoir-overflow)
  - [](reservoir-schedule)
  - [](reservoir-complex-ramping)
  - [](creek-intake-example)
  

## References
  - Modelling overflow using mixed integer programming in short-term hydropower scheduling {cite}`Litlabo2023`
  

## Attributes

In [1]:
from IPython.core.display import HTML
HTML("""<table id="reservoir-table" class="display compact"></table>
<script>
enableDataTable(
  "#reservoir-table",
  "/_static/data/reservoir-attribute-table.json"
);
</script>
""")

(reservoir:latitude)=
### latitude
Reserved for future use (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:longitude)=
### longitude
Reserved for future use (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:max_vol)=
### max_vol
Maximum volume of the reservoir (xUnit: MM3, yUnit: MM3)


(reservoir:lrl)=
### lrl
Lowest Regulation Level (meter above sea level) of the reservoir (xUnit: METER, yUnit: METER)


(reservoir:hrl)=
### hrl
Highest Regulation Level (meter above sea level) of the reservoir (xUnit: METER, yUnit: METER)


(reservoir:vol_head)=
### vol_head
The volume (Mm3) and water level (meter above sea level) relation of the reservoir. The list should cover all feasible reservoir level values so that the volume-head conversion is always successful. (xUnit: MM3, yUnit: METER)


(reservoir:head_area)=
### head_area
The water level (meter above sea level) and surface area (Km2) relation of the reservoir (xUnit: METER, yUnit: KM2)


(reservoir:elevation_adjustment)=
### elevation_adjustment
Adjustment for the lowest regulation level (lrl), highest regulation level (hrl), and the volume (Mm3) and water level (meter above sea level) relation of the reservoir (xUnit: NO_UNIT, yUnit: METER)


(reservoir:start_vol)=
### start_vol
Reservoir start volume. If start_vol and start_head are both defined, the value of the prefer_start_vol attribute on global_settings will decide which is used (xUnit: MM3, yUnit: MM3)


(reservoir:start_head)=
### start_head
Reservoir start water level (meter above sea level). If start_vol and start_head are both defined, the value of the prefer_start_vol attribute on global_settings will decide which is used (xUnit: METER, yUnit: METER)


(reservoir:inflow)=
### inflow
Natural inflow to reservoir (xUnit: NO_UNIT, yUnit: M3/S)


(reservoir:inflow_flag)=
### inflow_flag
Flag determining whether the inflow to a reservoir should be used as input or calculated as output in the simulation: 0 = input; 1 = output (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:sim_inflow_flag)=
### sim_inflow_flag
Flag determining whether inflow should be simulated to reservoir or not (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:flow_descr)=
### flow_descr
The water level (meter above sea level) and overflow (m3/s) relation of the reservoir. Only used when a spill gate is connected, please see the overflow modelling example (xUnit: METER, yUnit: M3/S)


(reservoir:overflow_mip_flag)=
### overflow_mip_flag
Flag determining whether the binary variables should be used to prevent non-physical spill (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:overflow_cost)=
### overflow_cost
Overflow cost for the reservoir (xUnit: NO_UNIT, yUnit: NOK/MM3)


(reservoir:overflow_cost_flag)=
### overflow_cost_flag
Flag determining whether overflow cost for this reservoir should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:min_vol_constr)=
### min_vol_constr
Time-dependent minimum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:min_vol_constr_flag)=
### min_vol_constr_flag
Flag determining whether the time-dependent minimum volume limit for the reservoir should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:max_vol_constr)=
### max_vol_constr
Time-dependent maximum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:max_vol_constr_flag)=
### max_vol_constr_flag
Flag determining whether the time-dependent maximum volume limit for the reservoir should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:min_head_constr)=
### min_head_constr
Time-dependent minimum water level limit for the reservoir. The min_vol_constr attribute is preferred if it is present for the same reservoir. (xUnit: NO_UNIT, yUnit: METER)


(reservoir:min_head_constr_flag)=
### min_head_constr_flag
Flag determining whether the time-dependent minimum water level limit for the reservoir should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:max_head_constr)=
### max_head_constr
Time-dependent maximum water level limit for the reservoir. The max_vol_constr attribute is preferred if it is present for the same reservoir. (xUnit: NO_UNIT, yUnit: METER)


(reservoir:max_head_constr_flag)=
### max_head_constr_flag
Flag determining whether the time-dependent maximum water level limit for the reservoir should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:tactical_limit_min)=
### tactical_limit_min
Tactical (soft) minimum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:tactical_limit_min_flag)=
### tactical_limit_min_flag
Flag determining whether the tactical minimum volume limit should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:tactical_cost_min)=
### tactical_cost_min
Given penalty cost for violating the tactical minimum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: NOK/MM3H)


(reservoir:tactical_cost_min_flag)=
### tactical_cost_min_flag
Flag determining whether the penalty cost for violating the tactical minimum volume limit should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:tactical_limit_max)=
### tactical_limit_max
Tactical (soft) maximum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:tactical_limit_max_flag)=
### tactical_limit_max_flag
Flag determining whether the tactical maximum volume limit should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:tactical_cost_max)=
### tactical_cost_max
Given penalty cost for violating the tactical maximum volume limit for the reservoir (xUnit: NO_UNIT, yUnit: NOK/MM3H)


(reservoir:tactical_cost_max_flag)=
### tactical_cost_max_flag
Flag determining whether the penalty cost for violating the tactical maximum volume limit should be included in the optimization model (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:tactical_level_limit_min)=
### tactical_level_limit_min
Tactical minimum level limit for the reservoir (xUnit: NO_UNIT, yUnit: METER)


(reservoir:tactical_level_limit_max)=
### tactical_level_limit_max
Tactical maximum level limit for the reservoir (xUnit: NO_UNIT, yUnit: METER)


(reservoir:upper_slack)=
### upper_slack
Used to expand the upper reservoir limit when running with an active reservoir schedule so that the volume can be between the schedule and upper_slack. (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:lower_slack)=
### lower_slack
Used to expand the lower reservoir limit when running with an active reservoir schedule so that the volume can be between the schedule and lower_slack. (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:schedule)=
### schedule
Reservoir volume schedule used to specify the volume of the reservoir in each time step. Must be combined with a schedule_flag to be active. (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:schedule_flag)=
### schedule_flag
Flag determining whether the reservoir volume schedule should be included in the optimization model: 0 = no schedule; 1 = the endpoint interval upper_slack and lower_slack is valid; 2 = reservoir volume schedule is valid anywhere during the optimization period (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:volume_schedule)=
### volume_schedule
Reservoir volume schedule used in the SHOP simulator (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:level_schedule)=
### level_schedule
Reservoir water level schedule used in the SHOP simulator (xUnit: NO_UNIT, yUnit: METER)


(reservoir:volume_ramping_up)=
### volume_ramping_up
Maximum limit for increase in reservoir volume per hour (xUnit: NO_UNIT, yUnit: MM3/HOUR)


(reservoir:volume_ramping_down)=
### volume_ramping_down
Maximum limit for decrease in reservoir volume per hour (xUnit: NO_UNIT, yUnit: MM3/HOUR)


(reservoir:level_ramping_up)=
### level_ramping_up
Maximum limit for increase in reservoir level per hour (xUnit: NO_UNIT, yUnit: METER/HOUR)


(reservoir:level_ramping_down)=
### level_ramping_down
Maximum limit for decrease in reservoir level per hour (xUnit: NO_UNIT, yUnit: METER/HOUR)


(reservoir:water_value_input)=
### water_value_input
The input water value description of water values referred to the sea. Can be a single constant value, a water value table (xy), or cut coefficients for a single or multiple price nodes. In the case of price dependent cut coefficients, the reference value of each xy in the xy_array should be the relevant price level. (xUnit: MM3, yUnit: NOK/MM3)


(reservoir:energy_value_input)=
### energy_value_input
The input local energy value of the reservoir which will be converted to a global water value internally. (xUnit: NOK/MWH, yUnit: NOK/MWH)


(reservoir:peak_volume_cost_curve)=
### peak_volume_cost_curve
A piece-wise constant increasing cost which is applied to the highest reservoir volume reached in the optimization horizon (xUnit: MM3, yUnit: NOK/MM3)


(reservoir:flood_volume_cost_curve)=
### flood_volume_cost_curve
A piece-wise constant increasing cost curve which is used to penalize the reservoir volume level in each hour of the optimzation (xUnit: MM3, yUnit: NOK/MM3)


(reservoir:evaporation_rate)=
### evaporation_rate
Evaporation rate of water from the reservoir (xUnit: NO_UNIT, yUnit: METER/HOUR)


(reservoir:level_rolling_ramping_penalty_cost)=
### level_rolling_ramping_penalty_cost
The penalty cost for breaking any rolling ramping constraint applied to the reservoir level (xUnit: NO_UNIT, yUnit: NOK/METER)


(reservoir:level_period_ramping_penalty_cost)=
### level_period_ramping_penalty_cost
The penalty cost for breaking any period ramping constraint applied to the reservoir level (xUnit: NO_UNIT, yUnit: NOK/METER)


(reservoir:average_level_rolling_ramping_up)=
### average_level_rolling_ramping_up
Input to specify rolling ramping constraints that constrain the reservoir level upwards from the average reservoir level in a rolling time window. The x-values represent the length of the rolling time window and the y-values specify the number of meters the reservoir level can increase above the average rolling level. Each (x, y) point in each xy curve represents a rolling ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:average_level_rolling_ramping_down)=
### average_level_rolling_ramping_down
Input to specify rolling ramping constraints that constrain the reservoir level downwards from the average reservoir level in a rolling time window. The x-values represent the length of the rolling time window and the y-values specify the number of meters the reservoir level can decrease below the average rolling level. Each (x, y) point in each xy curve represents a rolling ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:limit_level_rolling_ramping_up)=
### limit_level_rolling_ramping_up
Input to specify rolling ramping constraints that constrain the reservoir level upwards from the minimal reservoir level in a rolling time window. The x-values represent the length of the rolling time window and the y-values specify the number of meters the reservoir level can increase above the minimal rolling level. Each (x, y) point in each xy curve represents a rolling ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:limit_level_rolling_ramping_down)=
### limit_level_rolling_ramping_down
Input to specify rolling ramping constraints that constrain the reservoir level downwards from the maximal reservoir level in a rolling time window. The x-values represent the length of the rolling time window and the y-values specify the number of meters the reservoir level can decrease below the maximal rolling level. Each (x, y) point in each xy curve represents a rolling ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:average_level_period_ramping_up)=
### average_level_period_ramping_up
Input to specify period ramping constraints that constrain the reservoir level upwards from the average reservoir level in a fixed time window. The x-values represent the length of the fixed time window and the y-values specify the number of meters the reservoir level can increase above the average level in the previous fixed time period. Each (x, y) point in each xy curve represents a period ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:average_level_period_ramping_down)=
### average_level_period_ramping_down
Input to specify period ramping constraints that constrain the reservoir level downwards from the average reservoir level in a fixed time window. The x-values represent the length of the fixed time window and the y-values specify the number of meters the reservoir level can decrease below the average level in the previous fixed time period. Each (x, y) point in each xy curve represents a period ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:limit_level_period_ramping_up)=
### limit_level_period_ramping_up
Input to specify period ramping constraints that constrain the reservoir level upwards from the minimal reservoir level in a fixed time window. The x-values represent the length of the fixed time window and the y-values specify the number of meters the reservoir level can increase above the minimal level in the previous fixed time period. Each (x, y) point in each xy curve represents a period ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:limit_level_period_ramping_down)=
### limit_level_period_ramping_down
Input to specify period ramping constraints that constrain the reservoir level downwards from the maximal reservoir level in a fixed time window. The x-values represent the length of the fixed time window and the y-values specify the number of meters the reservoir level can decrease below the maximal level in the previous fixed time period. Each (x, y) point in each xy curve represents a period ramping constraint. (xUnit: MINUTE, yUnit: METER)


(reservoir:historical_level)=
### historical_level
The reservoir level for times before the optimization start. The input start volume or start level of the reservoir will override any value in this time series that corresponds to the start time of the optimization, values inside the optimization horizon are ignored. The datatype of this attribute changed from xy to txy in version 15.3.1.0 (xUnit: NO_UNIT, yUnit: METER)


(reservoir:average_level_period_ramping_up_offset)=
### average_level_period_ramping_up_offset
The y-values must be the same as the period lengths used in the average_level_period_ramping_up attribute, while the strings are timestamps that specify when the first whole ramping period starts for each of the average ramping up period constraints. (xUnit: MINUTE, yUnit: MINUTE)


(reservoir:average_level_period_ramping_down_offset)=
### average_level_period_ramping_down_offset
The y-values must be the same as the period lengths used in the average_level_period_ramping_down attribute, while the strings are timestamps that specify when the first whole ramping period starts for each of the average ramping down period constraints. (xUnit: MINUTE, yUnit: MINUTE)


(reservoir:limit_level_period_ramping_up_offset)=
### limit_level_period_ramping_up_offset
The y-values must be the same as the period lengths used in the limit_level_period_ramping_up attribute, while the strings are timestamps that specify when the first whole ramping period starts for each of the limit ramping up period constraints. (xUnit: MINUTE, yUnit: MINUTE)


(reservoir:limit_level_period_ramping_down_offset)=
### limit_level_period_ramping_down_offset
The y-values must be the same as the period lengths used in the limit_level_period_ramping_down attribute, while the strings are timestamps that specify when the first whole ramping period starts for each of the limit ramping up period constraints. (xUnit: MINUTE, yUnit: MINUTE)


(reservoir:volume_nonseq_ramping_limit_up)=
### volume_nonseq_ramping_limit_up
Limit volume ramping between two non-sequential time steps. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: MM3)


(reservoir:volume_nonseq_ramping_limit_down)=
### volume_nonseq_ramping_limit_down
Limit volume ramping between two non-sequential time steps. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: MM3)


(reservoir:volume_amplitude_ramping_limit_up)=
### volume_amplitude_ramping_limit_up
Limit volume ramping between in time interval. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: MM3)


(reservoir:volume_amplitude_ramping_limit_down)=
### volume_amplitude_ramping_limit_down
Limit volume ramping between in time interval. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: MM3)


(reservoir:level_nonseq_ramping_limit_up)=
### level_nonseq_ramping_limit_up
Limit level ramping between two non-sequential time steps. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: METER)


(reservoir:level_nonseq_ramping_limit_down)=
### level_nonseq_ramping_limit_down
Limit level ramping between two non-sequential time steps. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: METER)


(reservoir:level_amplitude_ramping_limit_up)=
### level_amplitude_ramping_limit_up
Limit level ramping between in time interval. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: METER)


(reservoir:level_amplitude_ramping_limit_down)=
### level_amplitude_ramping_limit_down
Limit level ramping between in time interval. Start time is given by time T, duration by X and ramping by Y. (xUnit: MINUTE, yUnit: METER)


(reservoir:storage)=
### storage
Resulting reservoir volume, includes both the start volume and the final end volume in the optimization (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:sim_storage)=
### sim_storage
Simulated reservoir volume (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:head)=
### head
Resulting reservoir water level (meter above sea level), calculated by converting the volume of the reservoir with the vol_head_curve (xUnit: NO_UNIT, yUnit: METER)


(reservoir:area)=
### area
Resulting reservoir surface area (km2), used to calculate evaporation (xUnit: NO_UNIT, yUnit: KM2)


(reservoir:sim_head)=
### sim_head
Simulated reservoir water level (meter above sea level) (xUnit: NO_UNIT, yUnit: METER)


(reservoir:sim_inflow)=
### sim_inflow
Simulated inflow to reservoir (xUnit: NO_UNIT, yUnit: M3/S)


(reservoir:endpoint_penalty)=
### endpoint_penalty
Resulting penalty when the maximum or minimum volume limit for the reservoir at the end of the optimization period is violated (xUnit: MM3, yUnit: MM3)


(reservoir:penalty)=
### penalty
Resulting penalty when the maximum or minimum volume limit for the reservoir during the optimization period is violated (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:tactical_penalty_up)=
### tactical_penalty_up
Resulting penalty when the tactical maximum volume limit for the reservoir is violated (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:tactical_penalty_down)=
### tactical_penalty_down
Resulting penalty when the tactical minimum volume limit for the reservoir is violated (xUnit: NO_UNIT, yUnit: MM3)


(reservoir:end_penalty)=
### end_penalty
Resulting penalty cost when the maximum or minimum volume limit for the reservoir at the end of the optimization period is violated (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:penalty_nok)=
### penalty_nok
Resulting penalty cost when the maximum or minimum volume limit for the reservoir during the optimization period is violated (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:tactical_penalty)=
### tactical_penalty
Resulting penalty cost when the tactical maximum or minimum volume limit for the reservoir is violated (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:water_value_global_result)=
### water_value_global_result
Marginal cost of 1 Mm3 of the water in the reservoir calculated using the sum of the best efficiency point of all cascaded plants below this reservoir (xUnit: NO_UNIT, yUnit: NOK/MM3)


(reservoir:water_value_local_result)=
### water_value_local_result
Marginal cost of 1 Mm3 of the water discharged from the reservoir through the downstream plant (xUnit: NO_UNIT, yUnit: NOK/MM3)


(reservoir:energy_value_local_result)=
### energy_value_local_result
Marginal cost of 1 MWh power that generated from the water in the reservoir through the downstream plant (xUnit: NO_UNIT, yUnit: NOK/MWH)


(reservoir:end_value)=
### end_value
Value of reservoir contents at the end of the optimization period (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:change_in_end_value)=
### change_in_end_value
Relative change in value of reservoir contents between the start and the end of the optimization horizon (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:vow_in_transit)=
### vow_in_transit
Value of delayed water on its way to this reservoir after the end of the optimization period (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:calc_global_water_value)=
### calc_global_water_value
The resulting global water value of the reservoir after the local energy value has been converted internally based on the energy_conversion_factor reservoir attribute. (xUnit: NOK/MM3, yUnit: NOK/MM3)


(reservoir:energy_conversion_factor)=
### energy_conversion_factor
The calculated conversion factor between MWh and Mm3 based on the first plant below the reservoir and initial start head. (xUnit: MWH/MM3, yUnit: MWH/MM3)


(reservoir:water_value_cut_result)=
### water_value_cut_result
The resulting output water value cut coefficients when SHOP is used to create cuts. (xUnit: MM3, yUnit: NOK/MM3)


(reservoir:added_to_network)=
### added_to_network
Flag determining whether the model has determined that this reservoir is part of a tunnel network (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:network_no)=
### network_no
Network identification number set by the model to indicate which tunnel network this reservoir is part of (xUnit: NO_UNIT, yUnit: NO_UNIT)


(reservoir:peak_volume_penalty)=
### peak_volume_penalty
The peak volume penalty incurred for the reservoir, zero in all time steps except for when the reservoir volume peak occurs (xUnit: NO_UNIT, yUnit: NOK)


(reservoir:flood_volume_penalty)=
### flood_volume_penalty
The penalty incurred for the reservoir based on the optimized reservoir volume and the flood_volume_cost_curve (xUnit: NO_UNIT, yUnit: NOK)